# CS 506 BU ISE Project Solar Panel Regular Expressions

CS 506 Spring 2018

Team: 

Jason Lu (jasonlu6@bu.edu)

Hugh Qu (hughfang@bu.edu)

Zixin "Cindy" Ding (cindydxz@bu.edu)

# Proposal: 

CS 506 Final Project Proposal

CS 506 Spring 2018 

Computational Tools for Data Science 
 
Professor Adam Smith 
 
TF: Sofia Nikolakaki 2/20/2018
 
Contact: Michael Jay Walsh, Ph. D.
 
# Topic:  

Using Permit, Parcel, Census, data to populate building energy systems inventory Description of General Topic:
Our project is about using the databases provided from Carbon Free Boston in order to make an analysis of energy system changes over time for different types of Boston housing. The project will consist primarily of 3 main databases: Boston Assessor’s database of tax parcels (heating and cooling systems), Boston’s permit approval database, and a master database. In addition, we will employ the techniques taught from lecture of text mining, making a predictive model for the heating system, and use web scraping for the permit approval database. Finally, our project will answer the additional question, via measures of similarity, how well correlated is our data in comparison of the old energy system as opposed to the new energy system.

# Questions: From BU Spark:
    
1) What communities more like to have heat pumps (demographics, race, income level, etc. and geography)?
2) What communities are not benefitting from energy efficient systems?
3) How has this changed over time?

# From Our Group:

1) Does there exist a correlation between the installation of new energy system as opposed to the old energy system for Boston housing permits?
2) Will the number of people (occupants) living in Boston housing affect the heating and cooling system cost per family?

# For Michael:

1) How to access Zillow API?
2) How to access/understand the CSV entries?
3) What range of fiscal year should we use for property assessments? 4) What type of housing is inside the parcel data?

# Ideas for Specific Data Sets: Data sources:
1. Census American Housing Survey
2. Boston Building permits (text analysis for renovations involving installation of new energy systems) ( 358,472 entries, free to access)
3. Boston Property Assessments ( 170,910 entries, free to access )
4. Zillow API (description of energy systems)

# Tentative Design / Plan of Our Project: 

**Project Mockup**: on github website 

In [3]:
# imports 
import json
import csv 
import pandas as pd
from pandas import DataFrame as Df

# clustering imports 
from sklearn.cluster import KMeans
from sklearn import mixture
import scipy.cluster.hierarchy as hierarchy
import sklearn.metrics as metrics
from sklearn.preprocessing import MinMaxScaler

# plotting imports 
import sklearn.cluster 
import matplotlib 
import numpy as np
import scipy as sp
import matplotlib.pyplot as plt
# other imports 

# Source Code:

In [4]:
# sources: 

# (json.dumps):
# https://stackoverflow.com/questions/19697846/how-to-convert-csv-file-to-multiline-json

# (avoid the UTF-8 encoding error):
# https://stackoverflow.com/questions/5552555/unicodedecodeerror-invalid-continuation-byte

# (TFDIF Vectorizer and Histogram Count Vectorizer for frequency of words in comments):
# https://stackoverflow.com/questions/36572221/how-to-find-ngram-frequency-of-a-column-in-a-pandas-dataframe

# creating the master database (create and read CSV)
# https://pythonspot.com/files-spreadsheets-csv/

# deal with error larger than field limit problem
# https://stackoverflow.com/questions/15063936/
# csv-error-field-larger-than-field-limit-131072

# avoid the "np.nan is an invalid document, expected byte or unicode string" Value Type error 
# https://stackoverflow.com/questions/39303912/
# tfidfvectorizer-in-scikit-learn-valueerror-np-nan-is-an-invalid-document

# counter object for the histogram frequency 
# https://stackoverflow.com/questions/22303554/words-frequency-using-pandas-and-matplotlib

# counting unique values in a list
# https://stackoverflow.com/questions/12282232/
# how-do-i-count-unique-values-inside-an-array-in-python

# plotting a frequency histogram
# https://stackoverflow.com/questions/45080698/
# make-frequency-histogram-from-list-with-tuple-elements

# selecting rows from dataframe using only a specified column value 
# (masking method)
# https://stackoverflow.com/questions/17071871/
# select-rows-from-a-dataframe-based-on-values-in-a-column-in-pandas

# filtering rows containing a string pattern / regex in pandas dataframe 
# https://stackoverflow.com/questions/27975069/
# how-to-filter-rows-containing-a-string-pattern-from-a-pandas-dataframe

# regular expression: extract a data type from string in pandas 
# https://stackoverflow.com/questions/35376387/extract-int-from-string-in-pandas

In [5]:
# parse the assessor CSV file (ast2018full.csv)
index = 0
pid_index = {}
master_list = {}
# attributes in master database 
attr = ['parcel_id','zipcode','land_use','avg_total','living_area',
        'heat_type','r_ac','comments','longitude','latitude']

with open('ast2018full.csv',encoding='latin-1') as fp:
    a_reader = csv.reader(fp, dialect='excel')
    n = next(a_reader,None)
    for row in a_reader:
        try:
            pid_index[row[0].lstrip("0")] 
        except KeyError:
            # create new data 
            master_list[index] = {}
            master_list[index] = {attr[0]: row[0],attr[1]: row[7],
                              attr[2]:row[9],attr[3]:row[18],
                              attr[4]:row[24],attr[5]:row[41],
                              attr[6]:row[42]}
            pid_index[row[0].lstrip("0")] = index
            index += 1
        else:
            # overwrite existing data 
            p_index = pid_index[row[0].lstrip("0")]
            master_list[p_index] = {attr[0]: row[0],attr[1]: row[7],
                              attr[2]:row[9],attr[3]:row[18],
                              attr[4]:row[24],attr[5]:row[41],
                              attr[6]:row[42]}
fp.close()
print(len(pid_index))
print(index)

170134
170134


In [6]:
# parse the buildingpermits.csv file 
with open('buildingpermits.csv',newline='',encoding='latin-1') as assess_file:
    assess_reader = csv.reader(assess_file, dialect='excel')
    n = next(assess_reader,None)
    for row in assess_reader:
        try:
            pid_index[row[19].lstrip("0")] 
        except KeyError:
            # drop the data if parcel id not found in 
            # assessor database 
            pass
        else:
            # append information from building database to master database 
            index = pid_index[row[19].lstrip("0")]
            try:
                master_list[index][attr[7]]
            except KeyError:
                # if comment does not exist, add new comment 
                master_list[index][attr[7]] = row[4].replace('\t',' ').replace('\r',' ')
            else:
                # if comment exists, append comments 
                master_list[index][attr[7]] += " " + row[4].replace('\t',' ').replace('\r',' ')
            if row[20] != '':
                # get latitude and longitude from the location
                loc = row[20].lstrip('(').rstrip(')').split(',')
                master_list[index][attr[8]] = loc[0].replace(' ','')
                master_list[index][attr[9]] = loc[1].replace(' ','')
assess_file.close()
print(len(master_list))
print(master_list[0])

170134
{'parcel_id': '0100001000', 'zipcode': '02128', 'land_use': 'R3', 'avg_total': '483100', 'living_area': '2202', 'heat_type': 'W', 'r_ac': 'N', 'comments': 'replace three existing columns - replace existing plywood', 'longitude': '42.379400000', 'latitude': '-71.032600000'}


In [7]:
# open the building permits csv file for solar panel text extraction 
with open('buildingpermits.csv',newline='',encoding='latin-1') as csv_file:
    file_reader = csv.reader(csv_file, dialect='excel')
    for row in file_reader:
        print(row[1:2])
    # file_writer.writerow(attr)
    # for i in range(len(master_list)):
        # file_writer.writerow(master_list[i].values())
csv_file.close()

['WORKTYPE']
['COB']
['EXTREN']
['INTEXT']
['EXTDEM']
['INTEXT']
['EXTREN']
['INTREN']
['INTEXT']
['COB']
['OTHER']
['INTEXT']
['OTHER']
['OTHER']
['OTHER']
['NEWCON']
['INTREN']
['INTREN']
['INTEXT']
['EXTREN']
['EXTREN']
['INTREN']
['ADDITION']
['INTEXT']
['EXTREN']
['ERECT']
['INTEXT']
['OTHER']
['INTREN']
['OTHER']
['EXTREN']
['EXTREN']
['OTHER']
['ERECT']
['ERECT']
['ADDITION']
['SPRNK9']
['INTEXT']
['INTEXT']
['OTHER']
['SITE']
['INTREN']
['INTEXT']
['ADDITION']
['OTHER']
['INTREN']
['EXTREN']
['INTREN']
['OTHER']
['OTHER']
['INTREN']
['SPRINK']
['INTEXT']
['INTEXT']
['OTHER']
['INTEXT']
['INTREN']
['EXTREN']
['FA']
['SIGNES']
['OTHER']
['INTREN']
['INTEXT']
['INTEXT']
['OTHER']
['COB']
['FA']
['FA']
['INTREN']
['INTEXT']
['INTREN']
['SIGNES']
['OTHER']
['INTEXT']
['INTREN']
['OTHER']
['ADDITION']
['SPRINK']
['SPRINK']
['OTHER']
['INTEXT']
['INTREN']
['INTREN']
['SPRNK9']
['ADDITION']
['ADDITION']
['OTHER']
['FSTTRK']
['SPRINK']
['EXTREN']
['INTREN']
['INTEXT']
['INTREN']
['CHGOC

['INTREN']
['OTHER']
['OTHER']
['FENCE2']
['OTHER']
['OTHER']
['EXTREN']
['EXTREN']
['INTEXT']
['ADDITION']
['INTREN']
['INTEXT']
['INTREN']
['INTREN']
['INTREN']
['INTEXT']
['INTREN']
['INTEXT']
['EXTREN']
['OTHER']
['OTHER']
['INTEXT']
['INTREN']
['INTREN']
['INTREN']
['EXTREN']
['INTEXT']
['INTREN']
['INTREN']
['INTEXT']
['SPRINK']
['FA']
['OTHER']
['ADDITION']
['INTEXT']
['PLUMBING']
['INTREN']
['INTREN']
['CHGOCC']
['INTEXT']
['OTHER']
['SITE']
['SITE']
['INTREN']
['OTHER']
['INTREN']
['SPRINK']
['INTEXT']
['INTREN']
['OTHER']
['EXTREN']
['INTREN']
['OTHER']
['OTHER']
['INTREN']
['OTHER']
['INTEXT']
['INTREN']
['INTREN']
['INTREN']
['OTHER']
['OTHER']
['INTEXT']
['INTREN']
['INTEXT']
['OTHER']
['INTREN']
['INTEXT']
['INTREN']
['INTEXT']
['OTHER']
['EXTREN']
['CHGOCC']
['ADDITION']
['SPRINK']
['OTHER']
['NEWCON']
['INTEXT']
['INTEXT']
['INTEXT']
['INTREN']
['INTREN']
['OTHER']
['INTREN']
['INTEXT']
['INTREN']
['INTREN']
['INTREN']
['ADDITION']
['INTEXT']
['OTHER']
['INTREN']
['INTR

['INTREN']
['FSTTRK']
['INTEXT']
['EXTREN']
['INTREN']
['VIOL']
['SIGNES']
['INTEXT']
['ADDITION']
['FSTTRK']
['EXTREN']
['FSTTRK']
['INTREN']
['FA']
['FA']
['CHGOCC']
['CHGOCC']
['ROOF']
['SIGNES']
['SIGNES']
['FSTTRK']
['INTREN']
['INTREN']
['NROCC']
['FSTTRK']
['ADDITION']
['FSTTRK']
['FSTTRK']
['FSTTRK']
['OTHER']
['INTEXT']
['FSTTRK']
['NROCC']
['FSTTRK']
['TEMTRL']
['SIGNES']
['FSTTRK']
['CHGOCC']
['AWNING']
['CHGOCC']
['FSTTRK']
['SIGNES']
['NROCC']
['NROCC']
['NROCC']
['EXTREN']
['FA']
['FSTTRK']
['CHGOCC']
['OTHER']
['INTREN']
['CHGOCC']
['EXTREN']
['SIGNES']
['INTREN']
['INTEXT']
['INTEXT']
['FSTTRK']
['FSTTRK']
['INTEXT']
['OTHER']
['CHGOCC']
['CHGOCC']
['INTREN']
['NROCC']
['FSTTRK']
['CHGOCC']
['AWNING']
['INTEXT']
['OTHER']
['INTREN']
['FSTTRK']
['FSTTRK']
['CHGOCC']
['OTHER']
['FSTTRK']
['CHGOCC']
['INTREN']
['SD']
['CHGOCC']
['OTHER']
['ADDITION']
['FSTTRK']
['FSTTRK']
['FSTTRK']
['ADDITION']
['INTREN']
['FSTTRK']
['CHGOCC']
['INTREN']
['NROCC']
['SD']
['SD']
['SIGNES']

['CELL']
['CELL']
['CELL']
['CELL']
['SIGNES']
['SIGNES']
['SIGNES']
['SIGNES']
['SIGNES']
['CELL']
['CELL']
['CELL']
['CELL']
['CELL']
['CELL']
['CELL']
['CELL']
['FSTTRK']
['CELL']
['CELL']
['CELL']
['CELL']
['CHGOCC']
['FSTTRK']
['FSTTRK']
['FSTTRK']
['ADDITION']
['FSTTRK']
['CHGOCC']
['NROCC']
['INTREN']
['CELL']
['CELL']
['CELL']
['FSTTRK']
['INTEXT']
['SIGNES']
['VIOL']
['SD']
['INTEXT']
['FSTTRK']
['OTHER']
['INTREN']
['CHGOCC']
['INTREN']
['ADDITION']
['SPFT']
['SPFT']
['INTEXT']
['ADDITION']
['CHGOCC']
['FSTTRK']
['CHGOCC']
['ADDITION']
['CELL']
['CELL']
['CELL']
['INTEXT']
['CELL']
['CELL']
['INTREN']
['INTREN']
['CELL']
['CELL']
['CELL']
['INTREN']
['CHGOCC']
['CHGOCC']
['ADDITION']
['CHGOCC']
['INTEXT']
['INTEXT']
['INTEXT']
['INTEXT']
['INTEXT']
['CHGOCC']
['INTEXT']
['CHGOCC']
['NROCC']
['NROCC']
['INTREN']
['VIOL']
['FSTTRK']
['SPFT']
['CHGOCC']
['FSTTRK']
['INTREN']
['INTREN']
['INTREN']
['INTREN']
['INTREN']
['INTREN']
['INTREN']
['INTREN']
['INTREN']
['INTREN']
['ADDI

['FA']
['FSTTRK']
['SIGNES']
['FSTTRK']
['FSTTRK']
['FSTTRK']
['FSTTRK']
['EXTREN']
['CHGOCC']
['FSTTRK']
['INTREN']
['CHGOCC']
['INTREN']
['OTHER']
['NROCC']
['SIGNES']
['INTEXT']
['SIGNES']
['FSTTRK']
['CHGOCC']
['ADDITION']
['CHGOCC']
['FSTTRK']
['FSTTRK']
['INTREN']
['EXTREN']
['INTREN']
['FSTTRK']
['FSTTRK']
['SIGNES']
['SIGNES']
['EXTREN']
['FSTTRK']
['NROCC']
['SPRINK']
['EXTREN']
['FSTTRK']
['NROCC']
['INTREN']
['INTEXT']
['NROCC']
['OTHER']
['INTEXT']
['FSTTRK']
['CHGOCC']
['CHGOCC']
['NROCC']
['CHGOCC']
['FSTTRK']
['INTEXT']
['CHGOCC']
['NROCC']
['FSTTRK']
['INTREN']
['INTREN']
['NROCC']
['NROCC']
['NROCC']
['SIGNES']
['CHGOCC']
['CHGOCC']
['SIGNES']
['SIGNES']
['SIGNES']
['CHGOCC']
['SIGNES']
['SIGNES']
['FSTTRK']
['EXTREN']
['EXTREN']
['SPRINK']
['INTEXT']
['FSTTRK']
['FSTTRK']
['NROCC']
['ADDITION']
['INTEXT']
['ADDITION']
['FSTTRK']
['SIGNES']
['FSTTRK']
['CHGOCC']
['SD']
['SD']
['CHGOCC']
['INTDEM']
['FSTTRK']
['FSTTRK']
['NROCC']
['CHGOCC']
['INTDEM']
['SIGNES']
['NROCC

...

['INTEXT']
['SIDE']
['SIDE']
['INTEXT']
['INTREN']
['ROOF']
['INTREN']
['INTREN']
['OTHER']
['INTREN']
['INTEXT']
['INTREN']
['INTEXT']
['INTEXT']
['INTREN']
['EXTREN']
['INSUL']
['INSUL']
['INSUL']
['INSUL']
['INSUL']
['INSUL']
['INSUL']
['INTREN']
['EXTREN']
['EXTREN']
['OTHER']
['ROOF']
['INTREN']
['EXTREN']
['INTREN']
['INTREN']
['INTEXT']
['INTEXT']
['ROOF']
['FENCE']
['ROOF']
['INTREN']
['OTHER']
['INTREN']
['INTREN']
['ROOF']
['ROOF']
['EXTREN']
['OTHER']
['INTREN']
['ROOF']
['OTHER']
['COB']
['EXTREN']
['COB']
['INTREN']
['COB']
['OTHER']
['COB']
['EXTDEM']
['COB']
['INTREN']
['COB']
['COB']
['INTEXT']
['INTDEM']
['COB']
['COB']
['INTREN']
['INTREN']
['COB']
['INTEXT']
['INTEXT']
['SIDE']
['COB']
['ROOF']
['SIDE']
['COB']
['INTREN']
['COB']
['INTREN']
['INTREN']
['INSUL']
['FENCE']
['SIDE']
['INSUL']
['ROOF']
['SOL']
['INSUL']
['INTREN']
['OTHER']
['INTEXT']
['INTEXT']
['INTEXT']
['INTREN']
['SIDE']
['INTEXT']
['EXTREN']
['SIDE']
['OTHER']
['INTREN']
['INTREN']
['INTREN']
['ROO

['OTHER']
['OTHER']
['INTEXT']
['INTEXT']
['EXTREN']
['ROOF']
['OTHER']
['ROOF']
['INSUL']
['OTHER']
['INSUL']
['INTEXT']
['INSUL']
['OTHER']
['OTHER']
['SIDE']
['INTREN']
['INTREN']
['INTREN']
['OTHER']
['INTREN']
['OTHER']
['OTHER']
['INTREN']
['INTREN']
['ROOF']
['ROOF']
['EXTREN']
['COB']
['ROOF']
['INTEXT']
['EXTREN']
['OTHER']
['ROOF']
['INTEXT']
['OTHER']
['ROOF']
['OTHER']
['OTHER']
['EXTREN']
['INTREN']
['EXTREN']
['ROOF']
['SIDE']
['EXTREN']
['ROOF']
['ROOF']
['OTHER']
['INTEXT']
['INTREN']
['FENCE']
['INSUL']
['INSUL']
['EXTREN']
['OTHER']
['EXTREN']
['EXTDEM']
['INTREN']
['INTREN']
['EXTREN']
['INTREN']
['OTHER']
['INTREN']
['CANP']
['EXTREN']
['ROOF']
['OTHER']
['SPCEVE']
['INTREN']
['INTREN']
['INTREN']
['SPCEVE']
['INTEXT']
['INTDEM']
['OTHER']
['INTEXT']
['INTREN']
['INTREN']
['INSUL']
['EXTREN']
['INTDEM']
['INTREN']
['INTREN']
['ROOF']
['EXTREN']
['INTDEM']
['INTREN']
['INTEXT']
['INTREN']
['EXTREN']
['INTREN']
['INSUL']
['INSUL']
['EXTREN']
['ROOF']
['INTREN']
['INTR

['OTHER']
['ROOF']
['FENCE']
['INTREN']
['OTHER']
['INTREN']
['INTREN']
['INTREN']
['OTHER']
['ROOF']
['INTEXT']
['INTEXT']
['SIDE']
['INTEXT']
['INTREN']
['EXTREN']
['INTREN']
['INSUL']
['ROOF']
['INTREN']
['TEMTRL']
['ROOF']
['INSUL']
['INSUL']
['OTHER']
['INTREN']
['EXTREN']
['SIDE']
['OTHER']
['INSUL']
['INSUL']
['INSUL']
['INSUL']
['INSUL']
['OTHER']
['RNWSIG']
['OTHER']
['OTHER']
['INTDEM']
['ROOF']
['INTEXT']
['INTREN']
['EXTREN']
['EXTREN']
['INTDEM']
['GEN']
['INTREN']
['INSUL']
['INSUL']
['INTREN']
['INTEXT']
['EXTREN']
['INTEXT']
['INTREN']
['INTREN']
['EXTREN']
['INTDEM']
['INTREN']
['EXTDEM']
['INTREN']
['CANP']
['OTHER']
['OTHER']
['INSUL']
['OTHER']
['OTHER']
['INTREN']
['INTREN']
['INTREN']
['INTREN']
['INTREN']
['INTREN']
['INTREN']
['INTREN']
['INTREN']
['INTREN']
['INTREN']
['INTREN']
['INTREN']
['INTREN']
['INTREN']
['INTREN']
['INTREN']
['INTREN']
['INTREN']
['INTREN']
['INTREN']
['INTREN']
['INTREN']
['INTREN']
['INTREN']
['INTREN']
['INTREN']
['INTREN']
['INTREN'

['EXTREN']
['INTEXT']
['ROOF']
['INTREN']
['INTEXT']
['MAINT']
['INSUL']
['INSUL']
['INSUL']
['INTREN']
['ROOF']
['INTEXT']
['INTREN']
['INTEXT']
['EXTREN']
['INTREN']
['INTREN']
['OTHER']
['SIDE']
['INTREN']
['ROOF']
['INTREN']
['INTREN']
['INTREN']
['INTDEM']
['EXTREN']
['EXTREN']
['INTEXT']
['EXTREN']
['ROOF']
['INTDEM']
['INTREN']
['INSUL']
['INSUL']
['INTEXT']
['INTREN']
['INTREN']
['EXTREN']
['EXTREN']
['EXTREN']
['EXTREN']
['OTHER']
['INTREN']
['INTREN']
['OTHER']
['INTREN']
['ROOF']
['EXTREN']
['SITE']
['INTREN']
['INTEXT']
['FENCE']
['OTHER']
['OTHER']
['EXTDEM']
['TMPSER']
['ROOF']
['INTREN']
['INTREN']
['SITE']
['INTREN']
['INTREN']
['INTEXT']
['EXTREN']
['ROOF']
['INSUL']
['INSUL']
['ROOF']
['EXTREN']
['INTEXT']
['ROOF']
['INTREN']
['OTHER']
['INTEXT']
['EXTREN']
['SPCEVE']
['INTREN']
['INTREN']
['INTREN']
['INTDEM']
['ROOF']
['OTHER']
['OTHER']
['INTREN']
['EXTREN']
['FA']
['MAINT']
['EXTREN']
['EXTREN']
['FENCE']
['FENCE']
['EXTREN']
['EXTREN']
['EXTREN']
['ROOF']
['INTRE

['EXTREN']
['ROOF']
['OTHER']
['OTHER']
['OTHER']
['OTHER']
['OTHER']
['OTHER']
['OTHER']
['EXTREN']
['OTHER']
['OTHER']
['VIOL']
['OTHER']
['OTHER']
['OTHER']
['OTHER']
['OTHER']
['OTHER']
['SIDE']
['OTHER']
['OTHER']
['OTHER']
['OTHER']
['OTHER']
['OTHER']
['INTREN']
['INTREN']
['INTDEM']
['INSUL']
['OTHER']
['EXTREN']
['INTDEM']
['OTHER']
['INTREN']
['ROOF']
['ROOF']
['INTEXT']
['ROOF']
['ROOF']
['SIDE']
['ROOF']
['ROOF']
['ROOF']
['INTEXT']
['INTEXT']
['INTEXT']
['FA']
['INTREN']
['FENCE']
['INTREN']
['EXTREN']
['INTEXT']
['EXTREN']
['INTEXT']
['INTEXT']
['INTEXT']
['INSUL']
['INTEXT']
['INTEXT']
['INTREN']
['INTREN']
['ROOF']
['INTREN']
['MAINT']
['EXTREN']
['EXTREN']
['MAINT']
['EXTREN']
['EXTREN']
['ROOF']
['EXTREN']
['EXTREN']
['ROOF']
['VIOL']
['DRIVE']
['RESPAR']
['COMPAR']
['OTHER']
['COB']
['COB']
['COB']
['DRIVE']
['RESPAR']
['DRIVE']
['DRIVE']
['COMPAR']
['COMPAR']
['COMPAR']
['DRIVE']
['RESPAR']
['DRIVE']
['RESPAR']
['OSEAT']
['RESPAR']
['RESPAR']
['COMPAR']
['OTHER']
['

In [9]:
# import for dataframe and plots
import matplotlib.pyplot as plt 
import pandas as pd 
from pandas import DataFrame as Df

In [10]:
# filter out for only 'SOL' and print out the comments corresponding 
work = pd.read_csv('buildingpermits.csv',encoding='latin-1')
work 

/anaconda3/lib/python3.6/site-packages/IPython/core/interactiveshell.py:2698: DtypeWarning: Columns (17) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


PermitNumber  WORKTYPE           PermitTypeDescr  \
0           A100071       COB  Amendment to a Long Form   
1           A100137    EXTREN  Amendment to a Long Form   
2           A100764    INTEXT  Amendment to a Long Form   
3           A100858    EXTDEM  Amendment to a Long Form   
4           A101019    INTEXT  Amendment to a Long Form   
5           A101208    EXTREN  Amendment to a Long Form   
6           A101379    INTREN  Amendment to a Long Form   
7           A101551    INTEXT  Amendment to a Long Form   
8           A101691       COB  Amendment to a Long Form   
9           A101698     OTHER  Amendment to a Long Form   
10          A101847    INTEXT  Amendment to a Long Form   
11          A101982     OTHER  Amendment to a Long Form   
12          A102166     OTHER  Amendment to a Long Form   
13          A102168     OTHER  Amendment to a Long Form   
14          A102296    NEWCON  Amendment to a Long Form   
15          A102380    INTREN  Amendment to a Long Form   
16          A102730    INTREN  Amendment to a Long Form   
17          A103065    INTEXT  Amendment to a Long Form   
18          A103733    EXTREN  Amendment to a Long Form   
19          A103962    EXTREN  Amendment to a Long Form   
20          A103982    INTREN  Amendment to a Long Form   
21          A104226  ADDITION  Amendment to a Long Form   
22          A104527    INTEXT  Amendment to a Long Form   
23          A104779    EXTREN  Amendment to a Long Form   
24            A1048     ERECT  Amendment to a Long Form   
25          A105271    INTEXT  Amendment to a Long Form   
26          A105483     OTHER  Amendment to a Long Form   
27          A106989    INTREN  Amendment to a Long Form   
28          A106993     OTHER  Amendment to a Long Form   
29          A107043    EXTREN  Amendment to a Long Form   
...             ...       ...                       ...   
361788     U4990927     DRIVE           Use of Premises   
361789      U499139    CONVRT           Use of Premises   
361790      U499139    CONVRT           Use of Premises   
361791     U4991617     DRIVE           Use of Premises   
361792      U499188    CONVRT           Use of Premises   
361793      U499188    CONVRT           Use of Premises   
361794      U499236    CONVRT           Use of Premises   
361795      U499236    CONVRT           Use of Premises   
361796     U4993339     DRIVE           Use of Premises   
361797     U4994232     OTHER           Use of Premises   
361798      U499439    CONVRT           Use of Premises   
361799      U499439    CONVRT           Use of Premises   
361800     U4994890    COMPAR           Use of Premises   
361801     U4995521    TEMTRL           Use of Premises   
361802     U4995828     OTHER           Use of Premises   
361803     U4996405     DRIVE           Use of Premises   
361804     U4996624     DRIVE           Use of Premises   
361805     U4996882    COMPAR           Use of Premises   
361806     U4997026     DRIVE           Use of Premises   
361807     U4997224     OTHER           Use of Premises   
361808      U499735    CONVRT           Use of Premises   
361809      U499735    CONVRT           Use of Premises   
361810      U499745    CONVRT           Use of Premises   
361811      U499745    CONVRT           Use of Premises   
361812      U499778    CONVRT           Use of Premises   
361813      U499778    CONVRT           Use of Premises   
361814      U499931    CONVRT           Use of Premises   
361815      U499931    CONVRT           Use of Premises   
361816     U4999318      VIOL           Use of Premises   
361817     U4999352     DRIVE           Use of Premises   

                           DESCRIPTION  \
0                       City of Boston   
1               Renovations - Exterior   
2               Interior/Exterior Work   
3                Demolition - Exterior   
4               Interior/Exterior Work   
5               Renovations - Exterior   
6           Renovations -Interior  NSC   
7           

In [11]:
# avoid reading in NaN values 
filter_work = work[work['WORKTYPE'].notnull()]
filter_work = filter_work[filter_work['Comments'].notnull()]
filter_work.head(10)

PermitNumber WORKTYPE           PermitTypeDescr                 DESCRIPTION  \
0      A100071      COB  Amendment to a Long Form              City of Boston   
1      A100137   EXTREN  Amendment to a Long Form      Renovations - Exterior   
2      A100764   INTEXT  Amendment to a Long Form      Interior/Exterior Work   
3      A100858   EXTDEM  Amendment to a Long Form       Demolition - Exterior   
4      A101019   INTEXT  Amendment to a Long Form      Interior/Exterior Work   
5      A101208   EXTREN  Amendment to a Long Form      Renovations - Exterior   
6      A101379   INTREN  Amendment to a Long Form  Renovations -Interior  NSC   
7      A101551   INTEXT  Amendment to a Long Form      Interior/Exterior Work   
8      A101691      COB  Amendment to a Long Form              City of Boston   
9      A101698    OTHER  Amendment to a Long Form                       Other   

                                            Comments  \
0  Change connector link layout from attached enc...   
1  Landscaping/stonework - amending permit #2801/...   
2  Interior and exterior work as indicated on dra...   
3  Landmark letter and permit submittal on existi...   
4       Amendment to add bathroom  bedroom 3rd floor   
5  Amending alt77244/2011 - changes being made to...   
6  Amend Long Form Permit 10-0840 As Follows: Mod...   
7  Finishing basement;as part of the first floor ...   
8                       New Trash Compactor and Lift   
9  application to amend existing permit # ALT 767...   

                  APPLICANT  DECLARED_VALUATION  TOTAL_FEES  \
0         Renee Santeusanio             40000.0       429.0   
1                       NaN             15000.0       206.0   
2           Gregory Pomeroy            750000.0      7565.0   
3               Arthur Choo                 0.0        20.0   
4               JOHN MAHONY              4000.0        75.0   
5              Mike Zaisser               600.0        32.0   
6            Stephen Weinig            200000.0      2092.0   
7         Christine McMahon             50000.0       562.0   
8        Paul Hardiman  Jr.             63444.0       669.0   
9  Garland Building Company                 0.0        20.0   

           ISSUED_DATE      EXPIRATION_DATE              ...                \
0  2011-11-04 11:04:58  2012-05-04 00:00:00              ...                 
1  2013-01-03 14:13:09  2013-07-03 00:00:00              ...                 
2  2012-01-05 10:57:44  2012-07-05 00:00:00              ...                 
3  2012-08-21 12:27:59  2013-02-21 00:00:00              ...                 
4  2011-11-25 11:20:47  2012-05-25 00:00:00              ...                 
5  2011-10-21 15:49:49  2012-04-21 00:00:00              ...                 
6  2012-07-11 13:29:18  2013-01-11 00:00:00              ...                 
7  2012-04-26 18:06:35  2012-10-26 00:00:00              ...                 
8  2011-11-15 12:01:55  2012-05-15 00:00:00              ...                 
9  2011-11-30 13:36:54  2012-05-30 00:00:00              ...                 

                         OWNER OCCUPANCYTYPE sq_feet  \
0               CITY OF BOSTON          Comm   170.0   
1                  MIARA SIMON        1-2FAM     0.0   
2      CARSON DAVID THOMAS  TS        1-2FAM  3663.0   
3          SDS HOSPITALITY LLC          Comm     0.0   
4             TROTMAN GERALD A        1-2FAM  1950.0   
5               SMYTHE ALICE P        1-2FAM     0.0   
6                  DYER DENNIS         Mixed     0.0   
7  ONE-08 N STREET CONDOMINIUM        1-2FAM   680.0   
8     BOSTON REDEVELOPMNT AUTH         Multi     0.0   
9          99 SUMMER OWNER LLC          Comm  1500.0   

                    ADDRESS           CITY STATE    ZIP Property_ID  \
0        175  W Boundary RD   West Roxbury    MA  02132     17268.0   
1  14    William Jackson AV       Brighton    MA  02135    149852.0   
2         81    Chestnut ST         Boston    MA  02108     31492.0   
3      81   S Huntington AV  Jamaica Pl

In [12]:
# reading the columns with only 'SOL' from worktype and corresponding comments 
# print out the capacity of the solar panels / energy systems 

# getting only the worktype and comments 
string_mask = filter_work[['WORKTYPE','Comments']]
string_mask

# filtering the worktype for 'SOL' only 

# regex expression of str.contains()
solar_mask = filter_work[filter_work['WORKTYPE'].str.contains("SOL*")]
solar_mask

PermitNumber WORKTYPE              PermitTypeDescr  \
93          A119050      SOL     Amendment to a Long Form   
94          A119052      SOL     Amendment to a Long Form   
109         A122886      SOL     Amendment to a Long Form   
414         A213657      SOL     Amendment to a Long Form   
845         A339942      SOL     Amendment to a Long Form   
2617      ALT100397      SOL  Long Form/Alteration Permit   
2634      ALT100586      SOL  Long Form/Alteration Permit   
2667      ALT101134      SOL  Long Form/Alteration Permit   
2897      ALT104402      SOL  Long Form/Alteration Permit   
2925      ALT104975      SOL  Long Form/Alteration Permit   
2944      ALT105161      SOL  Long Form/Alteration Permit   
3056      ALT107357      SOL  Long Form/Alteration Permit   
3118      ALT108459      SOL  Long Form/Alteration Permit   
3145      ALT109015      SOL  Long Form/Alteration Permit   
3303      ALT112649      SOL  Long Form/Alteration Permit   
3346      ALT113576      SOL  Long Form/Alteration Permit   
3477      ALT115384      SOL  Long Form/Alteration Permit   
3616      ALT118753      SOL  Long Form/Alteration Permit   
3637      ALT119005      SOL  Long Form/Alteration Permit   
3788      ALT122085      SOL  Long Form/Alteration Permit   
3832      ALT122849      SOL  Long Form/Alteration Permit   
3999      ALT125543      SOL  Long Form/Alteration Permit   
4084      ALT127373      SOL  Long Form/Alteration Permit   
4096      ALT127638      SOL  Long Form/Alteration Permit   
4610      ALT145762      SOL  Long Form/Alteration Permit   
4652      ALT147320      SOL  Long Form/Alteration Permit   
5080      ALT162195      SOL  Long Form/Alteration Permit   
5319      ALT170322      SOL  Long Form/Alteration Permit   
5320      ALT170338      SOL  Long Form/Alteration Permit   
5458      ALT174901      SOL  Long Form/Alteration Permit   
...             ...      ...                          ...   
355355     SF798878      SOL       Short Form Bldg Permit   
355357     SF798900      SOL       Short Form Bldg Permit   
355373     SF798965      SOL       Short Form Bldg Permit   
355402     SF799272      SOL       Short Form Bldg Permit   
355408     SF799327      SOL       Short Form Bldg Permit   
355441     SF799513      SOL       Short Form Bldg Permit   
355458     SF799672      SOL       Short Form Bldg Permit   
355469     SF799780      SOL       Short Form Bldg Permit   
355511     SF800124      SOL       Short Form Bldg Permit   
355621     SF801315      SOL       Short Form Bldg Permit   
355629     SF801363      SOL       Short Form Bldg Permit   
355743     SF802409      SOL       Short Form Bldg Permit   
355753     SF802496      SOL       Short Form Bldg Permit   
355759     SF802511      SOL       Short Form Bldg Permit   
355837     SF803143      SOL       Short Form Bldg Permit   
355899     SF803531      SOL       Short Form Bldg Permit   
355905     SF803586      SOL       Short Form Bldg Permit   
355940     SF803976      SOL       Short Form Bldg Permit   
355966     SF804134      SOL       Short Form Bldg Permit   
356004     SF804394      SOL       Short Form Bldg Permit   
356073     SF804822      SOL       Short Form Bldg Permit   
356189     SF805717      SOL       Short Form Bldg Permit   
356413     SF807556      SOL       Short Form Bldg Permit   
356592     SF809322      SOL       Short Form Bldg Permit   
357992      SF86961  TMPUSOC       Short Form Bldg Permit   
358094      SF87332  TMPUSOC       Short Form Bldg Permit   
359044      SF91948      SOL       Short Form Bldg Permit   
359433      SF93661  TMPUSOC       Short Form Bldg Permit   
359600      SF94180      SOL       Short Form Bldg Permit   
361166    U49308891  TMPUSOC              Use of Premises   

                          DESCRIPTION  \
93                       Solar Panels   
94                       Solar Panels   
109                      Solar Panels   
414                      Solar Panels   
845                

In [13]:
# filter within comments for word "solar" and similarity measures
# using the fuzzywuzzy (Levenshtein distance) and difflib Python library modules 

# sources (Mentor Adam Pollack Suggestion): 
# https://pypi.python.org/pypi/fuzzywuzzy
# http://chairnerd.seatgeek.com/fuzzywuzzy-fuzzy-string-matching-in-python/

# imports 
import fuzzywuzzy as fuzz
# import for disimilarity / similarity matching
from difflib import SequenceMatcher 
# regular expression import 
import re
# import pandas 
import pandas as pd 

In [14]:
# get all of the comments into a list format 
df = solar_mask['Comments']
df

solar_filter = filter_work[filter_work['Comments'].str.contains("solar*")]
solar_filter

PermitNumber  WORKTYPE              PermitTypeDescr  \
109         A122886       SOL     Amendment to a Long Form   
414         A213657       SOL     Amendment to a Long Form   
2617      ALT100397       SOL  Long Form/Alteration Permit   
2634      ALT100586       SOL  Long Form/Alteration Permit   
2667      ALT101134       SOL  Long Form/Alteration Permit   
2897      ALT104402       SOL  Long Form/Alteration Permit   
2901      ALT104441  ADDITION  Long Form/Alteration Permit   
2925      ALT104975       SOL  Long Form/Alteration Permit   
2944      ALT105161       SOL  Long Form/Alteration Permit   
3056      ALT107357       SOL  Long Form/Alteration Permit   
3066      ALT107488       COB  Long Form/Alteration Permit   
3118      ALT108459       SOL  Long Form/Alteration Permit   
3145      ALT109015       SOL  Long Form/Alteration Permit   
3346      ALT113576       SOL  Long Form/Alteration Permit   
3365       ALT11394    INTEXT  Long Form/Alteration Permit   
3366       ALT11394    INTEXT  Long Form/Alteration Permit   
3375       ALT11405    INTEXT  Long Form/Alteration Permit   
3376       ALT11405    INTEXT  Long Form/Alteration Permit   
3377       ALT11405    INTEXT  Long Form/Alteration Permit   
3378       ALT11406    INTEXT  Long Form/Alteration Permit   
3379       ALT11406    INTEXT  Long Form/Alteration Permit   
3380       ALT11407    INTEXT  Long Form/Alteration Permit   
3381       ALT11407    INTEXT  Long Form/Alteration Permit   
3382       ALT11407    INTEXT  Long Form/Alteration Permit   
3383       ALT11408    INTEXT  Long Form/Alteration Permit   
3384       ALT11408    INTEXT  Long Form/Alteration Permit   
3385       ALT11408    INTEXT  Long Form/Alteration Permit   
3388       ALT11409    INTEXT  Long Form/Alteration Permit   
3389       ALT11409    INTEXT  Long Form/Alteration Permit   
3390       ALT11409    INTEXT  Long Form/Alteration Permit   
...             ...       ...                          ...   
354925     SF794869    INTREN       Short Form Bldg Permit   
354939     SF795057       SOL       Short Form Bldg Permit   
355071     SF796050       SOL       Short Form Bldg Permit   
355087     SF796205       SOL       Short Form Bldg Permit   
355256     SF797858       SOL       Short Form Bldg Permit   
355258     SF797865       SOL       Short Form Bldg Permit   
355305     SF798422       SOL       Short Form Bldg Permit   
355355     SF798878       SOL       Short Form Bldg Permit   
355357     SF798900       SOL       Short Form Bldg Permit   
355373     SF798965       SOL       Short Form Bldg Permit   
355402     SF799272       SOL       Short Form Bldg Permit   
355408     SF799327       SOL       Short Form Bldg Permit   
355441     SF799513       SOL       Short Form Bldg Permit   
355458     SF799672       SOL       Short Form Bldg Permit   
355469     SF799780       SOL       Short Form Bldg Permit   
355511     SF800124       SOL       Short Form Bldg Permit   
355629     SF801363       SOL       Short Form Bldg Permit   
355743     SF802409       SOL       Short Form Bldg Permit   
355753     SF802496       SOL       Short Form Bldg Permit   
355759     SF802511       SOL       Short Form Bldg Permit   
355899     SF803531       SOL       Short Form Bldg Permit   
355905     SF803586       SOL       Short Form Bldg Permit   
355940     SF803976       SOL       Short Form Bldg Permit   
356004     SF804394       SOL       Short Form Bldg Permit   
356073     SF804822       SOL       Short Form Bldg Permit   
356189     SF805717       SOL       Short Form Bldg Permit   
356413     SF807556       SOL       Short Form Bldg Permit   
356737      SF81325    EXTREN       Short Form Bldg Permit   
358087      SF87293     OTHER       Short Form Bldg Permit   
359044      SF91948       SOL       Short Form Bldg Permit   

                       DESCRIPTION  \
109                   Solar Panels   
414                   Solar Panels   
2617                  Solar Panels   
2634      

In [1]:
# regular expression to filter each comment from solar panel description 
kw = solar_filter['Comments'].str.findall("(\S+)kW")
kw_0 = kw[0].str[0]
print(kw_0)

# find out how many entries have the word 'solar' and kilowatt solar capacity
# print(len(kw))

NameError: name 'solar_filter' is not defined

In [2]:
# extraction step for all float values 
extract = solar_filter['Comments'].str.extract('(\d+)').astype(float)
# filter out the NaNs 
extract_filter = solar_filter['Comments'].dropna()
# unit = solar_filter['Comments'].str.extract('(\kW \s+)').astype(str)
print(len(extract_filter))

# top 100 for simplicity
extract_filter[extract_filter.head(100)]
extract_filter.head(100)
# unit

NameError: name 'solar_filter' is not defined

In [17]:
# TO DO: fix this problem with some help from Adam Pollack / TF Sofia 

import re

#get only comments with kilowatts 

# only decimal values for the kilowatts 
# drop NaN values and empty lists 
kw_extract = extract_filter.str.findall('\d+\.\d+').dropna()
kw_extract
# kw_processed = extract_filter[extract_filter['Comments'].str.contains('kW*')]
# kw_processed = re.search('kW',extract_filter)
# .str.findall('kW')

# filter_work[filter_work['WORKTYPE'].str.contains("SOL*")]

# print(len(kw_processed))
# kw_processed

109             [9.6]
414       [31.2, 7.5]
2617               []
2634               []
2667          [27.69]
2897           [67.2]
2901               []
2925               []
2944         [195.84]
3056               []
3066               []
3118               []
3145          [24.48]
3346               []
3365               []
3366               []
3375               []
3376               []
3377               []
3378               []
3379               []
3380               []
3381               []
3382               []
3383               []
3384               []
3385               []
3388               []
3389               []
3390               []
             ...     
354925             []
354939         [9.57]
355071         [4.02]
355087        [4.060]
355256         [6.38]
355258         [2.23]
355305         [3.77]
355355         [3.92]
355357         [6.44]
355373         [2.95]
355402        [11.21]
355408          [8.4]
355441        [3.245]
355458         [6.09]
355469    